In [1]:
from __future__ import print_function

Load in the Python modules necessary to load the data (gzip and yaml), process the data (numpy and pandas), and plot the data (toyplot).

In [2]:
import gzip
import yaml
import numpy
import pandas
import toyplot.pdf

print("yaml version:    ", yaml.__version__)
print("numpy version:   ", numpy.__version__)
print("pandas version:  ", pandas.__version__)
print("toyplot version: ", toyplot.__version__)

yaml version:     3.12
numpy version:    1.14.0
pandas version:   0.22.0
toyplot version:  0.16.0


## Ingest Data

Load the data, which is output into a YAML file. (Actually, there are several runs that have been concatinated into a YAML file that has a sequence in its top level.) Most of these runs were performed with the miniGraphics application compiled at SHA 50630f94848b970cc8894eb0ceb84b47bcef20f5. The execption are the 234 composite runs (which was implemented afterward). These are compiled at SHA 4e647c2bb7fe5b77a1d5340c3480b146dcbf3947.

In [3]:
filename = 'miniGraphics-skybridge-vn-scaling.yaml.gz'
yaml_data = yaml.load(gzip.open(filename))
data = pandas.DataFrame(yaml_data)

Some of the original runs gave suspect results where the runs took much longer than expected. These appear to be transient issues in the system since a repeat of the run is closer to what is expected. To get more realistic results, I re-ran these conditions. So jettison these runs from the original data and load up the re-runs.

In [4]:
# Remove incorrect readings
data = data.loc[
    ((data['composite-algorithm'] != '2-3-SwapBase') |
     (data['num-processes'] != 4096) |
     (data['image-height'] != 1080)) &
    ((data['composite-algorithm'] != 'BinarySwapFold') |
     (data['num-processes'] != 2896) |
     (data['image-height'] != 1080)) &
    ((data['composite-algorithm'] != 'BinarySwapRemainder') |
     (data['num-processes'] != 2048) |
     (data['image-height'] != 1080)) &
    ((data['composite-algorithm'] != 'BinarySwapTelescoping') |
     (data['num-processes'] != 1616) |
     (data['image-height'] != 1080))
]
# Load correct readings and add them to the data
filename = 'miniGraphics-skybridge-vn-corrections.yaml.gz'
yaml_data = yaml.load(gzip.open(filename))
data = pandas.concat([data, pandas.DataFrame(yaml_data)], ignore_index=True)

The YAML data is hierarchical. The basic yaml reader to DataFrame just embeds dictionaries and lists in DataFrame columns. Fix that by expanding the data of these columns into new columns.

In [5]:
def expand_single_column(original_data, column_to_expand):

    expanded_data = pandas.DataFrame()
    for index in original_data.index:
        sub_table = pandas.DataFrame(original_data[column_to_expand][index])
        for column in original_data.columns:
            if column != column_to_expand:
                sub_table[column] = numpy.full(sub_table.index.shape,
                                               original_data[column][index],
                                               dtype=original_data[column].dtype)
        expanded_data = expanded_data.append(sub_table, ignore_index=True)
    return expanded_data

def flatten_table(original_data):
    flat_data = original_data
    for column_name in original_data.columns:
        if isinstance(flat_data[column_name][0], list):
            flat_data = expand_single_column(flat_data, column_name)
    return flat_data

In [6]:
data = flatten_table(data)

Add a column that gives a human-readable name to each image resolution.

In [7]:
image_height_names = {
    500: 'Desktop Window',
    1080: 'HDTV',
    4320: '8K UHD',
}

data['image-size'] = data['image-height'].map(image_height_names)

Rename the algorithms from the identifiers the program wrote out to the strings used in the paper. Note that there are some extras in the data that we are ignoring.

In [8]:
algorithm_names = {
    '2-3-SwapBase': '2-3 Swap',
    'BinarySwapFold': 'Naive',
    'BinarySwapTelescoping': 'Telescoping',
    'BinarySwapRemainder': 'Remainder',
    'BinarySwap234Schedule': '234 Composite',
    'IceTBase': 'IceT'
}

data['composite-algorithm'] = data['composite-algorithm'].map(algorithm_names)

Print a summary of the table data. There are multiple ways that Jupyter and pandas will report a summary of a table, but I find this method the most effective. It prints out every column. Then for all columns with a "small" number of unique values, it gives those values. This latter information really helps identify the proper way to group values.

In [9]:
import IPython.display

data_description = ''

for column_name in data.columns:
    data_description = data_description + '**' + column_name + '**: '
    unique_values = data[column_name].unique()
    if (len(unique_values) < 10):
        for value in unique_values:
            data_description = data_description + str(value) + ' '
    elif (numpy.issubdtype(unique_values.dtype, numpy.number)):
        data_description = (
            data_description +
            str(numpy.nanmin(unique_values)) + ' &ndash; ' +
            str(numpy.nanmax(unique_values)) + ' '
        )
    elif not pandas.isnull(unique_values).any():
        data_description = (
            data_description +
            str(numpy.min(unique_values)) + ' &ndash; ' +
            str(numpy.max(unique_values)) + ' '
        )
    data_description = data_description + ' \n'
    
IPython.display.display(IPython.display.Markdown(data_description))

**color-buffer-format**: byte  
**composite-algorithm**: Naive Remainder Telescoping 2-3 Swap IceT 234 Composite  
**composite-seconds**: 0.00119348 &ndash; 3.49925  
**compress-seconds**:  
**construct-tree-seconds**: 0.000182052 &ndash; 0.0610641  
**depth-buffer-format**: float  
**gather-seconds**: 0.00071677 &ndash; 3.45673  
**geometry**: box  
**geometry-distribution**: duplicate  
**geometry-overlap**: -0.05  
**icet-copy-result-seconds**:  
**image-compression**: True False  
**image-height**: 288 1080 4320  
**image-width**: 512 1920 7680  
**num-processes**: 128 &ndash; 8192  
**num-triangles**: 1536 &ndash; 98304  
**paint-seconds**: 0.00011823 &ndash; 0.147793  
**painter**: simple  
**partial-composite-seconds**: 0.000293153 &ndash; 0.86969  
**phi-rotation**: -178.406 &ndash; 136.756  
**random-seed**: 17627  
**rendering-order-dependent**: False  
**start-time**: 2018-05-30T02:23:10.000000000 &ndash; 2018-06-08T12:10:45.000000000  
**theta-rotation**: -177.945 &ndash; 179.418  
**total-seconds**: 0.00146716 &ndash; 3.59942  
**trial-num**: 0 &ndash; 19  
**uncompress-seconds**:  
**zoom**: 1.5  
**image-size**: nan HDTV 8K UHD  


## Plot Data

We are plotting the time it takes to do a "partial composite" (that is the time to blend all the pixels, but the pixels are left distributed across all the processes).

The first thing we want to do is to average the time it took over all trials. This is easily done with a pivot table.

In [10]:
average_partial_composite = data.pivot_table(
    values='partial-composite-seconds',
    index='num-processes',
    columns=[
        'image-size',
        'composite-algorithm',
    ],
    aggfunc='mean',
)

print(average_partial_composite.index)
print(average_partial_composite.columns)

Int64Index([ 128,  160,  176,  192,  224,  256,  272,  320,  352,  400,  448,
             512,  560,  640,  720,  800,  912, 1024, 1136, 1280, 1440, 1616,
            1824, 2048, 2288, 2576, 2896, 3248, 3648, 4096, 4592, 5152, 5792,
            6496, 7296, 8192],
           dtype='int64', name=u'num-processes')
MultiIndex(levels=[[u'8K UHD', u'HDTV'], [u'2-3 Swap', u'234 Composite', u'IceT', u'Naive', u'Remainder', u'Telescoping']],
           labels=[[0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1], [0, 1, 2, 3, 4, 5, 0, 1, 2, 3, 4, 5]],
           names=[u'image-size', u'composite-algorithm'])


Make a grouping structure of the data so we can pull out the actual data values for each trial.

In [11]:
grouped_data = data.groupby(['image-size', 'composite-algorithm'])

Plot data.

In [12]:
image_size = 'HDTV'
algorithms = ['2-3 Swap', 'Naive', 'Remainder', 'Telescoping', '234 Composite', 'IceT']

canvas = toyplot.Canvas('4.5in', '3in')

axes = canvas.cartesian(
    xlabel='Number of Processes',
    ylabel='Partial Composite Time (seconds)',
    xscale='log',
    bounds=(45,-15,15,-50),
)

#axes.x.ticks.locator = toyplot.locator.Log(base=2, format='{:.0f}')
axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=[128, 256, 512, 1024, 2048, 4096, 8192],
)
axes.y.domain.min = 0

for algorithm in algorithms:
    # Plot line following average
    data_series = average_partial_composite[image_size, algorithm]
    x = data_series.index
    y = numpy.array(data_series)
    axes.plot(x, y)
    
    # Some adjustments for correct label placement
    if algorithm == 'Naive':
        vert_shift = '70%'
    elif algorithm == '234 Composite':
        vert_shift = '150%'
    elif algorithm == 'Telescoping':
        vert_shift = '-20%'
    elif algorithm == 'Remainder':
        vert_shift = '-100%'
    else:
        vert_shift = '0'
    
    # Put label at end of series
    axes.text(
        x[-1],
        y[-1],
        algorithm + '  ',
        style={
            'text-anchor':'start',
            '-toyplot-anchor-shift':'2px',
            'baseline-shift': vert_shift,
        },
    )
    
    # Put a dot at every recorded sample.
    scatter_data = data.loc[grouped_data.groups[(image_size, algorithm)]]
    x = scatter_data['num-processes']
    y = scatter_data['partial-composite-seconds']
    axes.scatterplot(x, y, opacity=1)

<path d="M 45.0 205.2249631166436 L 61.093195036721156 203.97416744545376 L 67.96700027797664 204.7997506635266 L 74.24229280630978 204.8001118961285 L 85.35969656228939 203.99997473614692 L 94.99002973739198 205.64263831258646 L 99.36229977241322 204.79394315477305 L 111.08322477411312 205.2481931516579 L 117.9570300153686 205.41180373319378 L 127.17641981083435 204.88349410613932 L 135.34972629968135 204.7041073853937 L 144.98005947478396 204.9248552390565 L 151.4429213364025 205.29304156853948 L 161.0732545115051 205.5191592837651 L 169.56781038673265 205.01511476206497 L 177.1664495482263 204.30409090625895 L 186.61625605085612 204.46566608101878 L 194.9700892121759 202.99847124095047 L 202.4559521693037 203.04828660610815 L 211.06328424889705 197.14454409803997 L 219.55784012412465 201.8175740782276 L 227.8741008084309 196.25960758476322 L 236.60628578824813 199.66403034777517 L 244.96011894956789 197.4939880129092 L 252.95209182927613 196.3105830623154 L 261.5026635271225 194.58345357805936 L 269.9474297089703 191.2233304362454 L 278.2202812350097 187.78205500105912 L 286.5963155256401 184.2648234645434 L 294.9501486869598 176.98793858173528 L 303.1938508553793 172.39364341519945 L 311.49269326451446 165.8296371786724 L 319.9374594463623 157.3848456132481 L 328.2103109724017 146.456698005059 L 336.586345263032 134.06902480281116 L 344.9401784243517 93.32777397729677" style="stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0;stroke-width:2.0"> 2-3 Swap <path d="M 45.0 206.83542836404868 L 61.093195036721156 185.67196338454636 L 67.96700027797664 185.2825060122363 L 74.24229280630978 185.97972661458138 L 85.35969656228939 185.89433678491773 L 94.99002973739198 207.27358266980676 L 99.36229977241322 186.78125313072408 L 111.08322477411312 186.68745074950465 L 117.9570300153686 187.36085778724782 L 127.17641981083435 187.19631633708397 L 135.34972629968135 187.28001115223108 L 144.98005947478396 207.90103675252016 L 151.4429213364025 187.5941376334841 L 161.0732545115051 187.78257600961956 L 169.56781038673265 187.95865606270172 L 177.1664495482263 187.76302082165154 L 186.61625605085612 188.0994117353868 L 194.9700892121759 208.23435024235854 L 202.4559521693037 188.21574252675913 L 211.06328424889705 188.1492340473253 L 219.55784012412465 188.1984033618681 L 227.8741008084309 187.85990410015825 L 236.60628578824813 187.9922993221437 L 244.96011894956789 207.55333300624275 L 252.95209182927613 187.7014167694666 L 261.5026635271225 187.52001548228725 L 269.9474297089703 187.07502554421643 L 278.2202812350097 186.74399754526308 L 286.5963155256401 185.54069701444183 L 294.9501486869598 205.15259850099062 L 303.1938508553793 185.47957923691325 L 311.49269326451446 184.64761192728 L 319.9374594463623 182.38225281297895 L 328.2103109724017 180.81776136094598 L 336.586345263032 178.2188734066016 L 344.9401784243517 201.0503993931691" style="stroke:rgb(98.8%,55.3%,38.4%);stroke-opacity:1.0;stroke-width:2.0"> Naive <g class="toyplot-Datum" style="fill:rgb(98.

In [13]:
toyplot.pdf.render(canvas, 'scaling-hdtv.pdf')

In [14]:
image_size = '8K UHD'
algorithms = ['2-3 Swap', 'Naive', 'Remainder', 'Telescoping', '234 Composite', 'IceT']

canvas = toyplot.Canvas('4.5in', '3in')

axes = canvas.cartesian(
    xlabel='Number of Processes',
    ylabel='Partial Composite Time (seconds)',
    xscale='log',
    bounds=(45,-15,15,-50),
)

#axes.x.ticks.locator = toyplot.locator.Log(base=2, format='{:.0f}')
axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=[128, 256, 512, 1024, 2048, 4096, 8192],
)
axes.y.domain.min = 0

for algorithm in algorithms:
    # Plot line following average
    data_series = average_partial_composite[image_size, algorithm]
    x = data_series.index
    y = numpy.array(data_series)
    axes.plot(x, y)
    
    if algorithm == 'Naive':
        vert_shift = '-30%'
    elif algorithm == '234 Composite':
        vert_shift = '50%'
    elif algorithm == 'Telescoping':
        vert_shift = '-160%'
    elif algorithm == 'Remainder':
        vert_shift = '-240%'
    else:
        vert_shift = '0'
    
    # Put label at end of series
    axes.text(
        x[-1],
        y[-1],
        algorithm + '  ',
        style={
            'text-anchor':'start',
            '-toyplot-anchor-shift':'2px',
            'baseline-shift': vert_shift,
        },
    )
    
    # Put a dot at every recorded sample.
    scatter_data = data.loc[grouped_data.groups[(image_size, algorithm)]]
    x = scatter_data['num-processes']
    y = scatter_data['partial-composite-seconds']
    axes.scatterplot(x, y, opacity=1)

<path d="M 45.0 132.72374416666668 L 61.093195036721156 128.8454148888889 L 67.96700027797664 127.99216733333334 L 74.24229280630978 129.44559461111112 L 85.35969656228939 129.55720611111113 L 94.99002973739198 135.4071527222222 L 99.36229977241322 131.83048050000002 L 111.08322477411312 132.3487448888889 L 117.9570300153686 132.15321105555557 L 127.17641981083435 132.5085243888889 L 135.34972629968135 133.46945616666667 L 144.98005947478396 137.02231694444447 L 151.4429213364025 135.02737133333338 L 161.0732545115051 136.14977988888893 L 169.56781038673265 133.85325155555554 L 177.1664495482263 133.6375733888889 L 186.61625605085612 136.63941355555556 L 194.9700892121759 139.40166499999998 L 202.4559521693037 137.6978335 L 211.06328424889705 137.42397711111113 L 219.55784012412465 136.48425511111117 L 227.8741008084309 133.7820773888889 L 236.60628578824813 133.32086383333336 L 244.96011894956789 139.73736672222222 L 252.95209182927613 138.67743533333336 L 261.5026635271225 137.52661905555559 L 269.9474297089703 136.35601772222222 L 278.2202812350097 134.22947733333336 L 286.5963155256401 136.56835088888892 L 294.9501486869598 132.37155283333334 L 303.1938508553793 133.34579027777778 L 311.49269326451446 133.92248066666664 L 319.9374594463623 131.248116 L 328.2103109724017 126.498439 L 336.586345263032 129.338567 L 344.9401784243517 127.34197366666669" style="stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0;stroke-width:2.0"> 2-3 Swap <path d="M 45.0 126.3981137777778 L 61.093195036721156 68.12004950000002 L 67.96700027797664 68.02883011111115 L 74.24229280630978 69.63407083333338 L 85.35969656228939 70.01917944444443 L 94.99002973739198 138.25750155555556 L 99.36229977241322 73.1599486111111 L 111.08322477411312 72.42211594444444 L 117.9570300153686 73.65178750000003 L 127.17641981083435 74.0119944444445 L 135.34972629968135 73.83064588888888 L 144.98005947478396 139.9580747777778 L 151.4429213364025 75.7177833888889 L 161.0732545115051 77.17614144444447 L 169.56781038673265 77.77535483333335 L 177.1664495482263 77.93948283333336 L 186.61625605085612 77.49268994444446 L 194.9700892121759 142.95996450000004 L 202.4559521693037 80.25693600000005 L 211.06328424889705 70.01709811111112 L 219.55784012412465 81.35425705555558 L 227.8741008084309 81.15726133333334 L 236.60628578824813 81.05950061111115 L 244.96011894956789 144.56427605555558 L 252.95209182927613 82.96657183333333 L 261.5026635271225 82.98784355555563 L 269.9474297089703 77.49625794444447 L 278.2202812350097 83.28407427777779 L 286.5963155256401 83.27966383333337 L 294.9501486869598 140.4405352777778 L 303.1938508553793 84.23201011111114 L 311.49269326451446 83.82254494444446 L 319.9374594463623 83.8659184444445 L 328.2103109724017 83.24884027777779 L 336.586345263032 83.15229366666671 L 344.9401784243517 144.7196575" style="stroke:rgb(98.8%,55.3%,38.4%);stroke-opacity:1.0;stroke-width:2.0"> Naive <g class="toyplot-Datum" style="fill:rgb(98.8%,55.3%,38.4%);fill-opacity:1.0;opacity:1.0;stroke:rgb(98.8%,55.3%,38.4%);stroke-opacity:1.0" transform="translate(286.59631

In [15]:
toyplot.pdf.render(canvas, 'scaling-8k.pdf')

## Gather Times

The previous plots only consider the composite time up to the point where the final image is distributed among many processes. The time to collect the data is also important. However, the cluster on which the experiments were run gave wildly inconsistent times for the gather operation that seem to have little to anything to do with the compositing. These plots show those gather times.

In [16]:
average_gather = data.pivot_table(
    values='gather-seconds',
    index='num-processes',
    columns=[
        'image-size',
        'composite-algorithm',
    ],
    aggfunc='mean',
)

print(average_gather.index)
print(average_gather.columns)

Int64Index([ 128,  160,  176,  192,  224,  256,  272,  320,  352,  400,  448,
             512,  560,  640,  720,  800,  912, 1024, 1136, 1280, 1440, 1616,
            1824, 2048, 2288, 2576, 2896, 3248, 3648, 4096, 4592, 5152, 5792,
            6496, 7296, 8192],
           dtype='int64', name=u'num-processes')
MultiIndex(levels=[[u'8K UHD', u'HDTV'], [u'2-3 Swap', u'234 Composite', u'IceT', u'Naive', u'Remainder', u'Telescoping']],
           labels=[[0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1], [0, 1, 2, 3, 4, 5, 0, 1, 2, 3, 4, 5]],
           names=[u'image-size', u'composite-algorithm'])


In [17]:
image_size = 'HDTV'
algorithms = ['2-3 Swap', 'Naive', 'Remainder', 'Telescoping', '234 Composite', 'IceT']

canvas = toyplot.Canvas('4.5in', '3in')

axes = canvas.cartesian(
    xlabel='Number of Processes',
    ylabel='Gather Time (seconds)',
    xscale='log',
    bounds=(45,-15,15,-50),
)

#axes.x.ticks.locator = toyplot.locator.Log(base=2, format='{:.0f}')
axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=[128, 256, 512, 1024, 2048, 4096, 8192],
)
axes.y.domain.min = 0

for algorithm in algorithms:
    # Plot line following average
    data_series = average_gather[image_size, algorithm]
    x = data_series.index
    y = numpy.array(data_series)
    axes.plot(x, y)
    
    # Some adjustments for correct label placement
    if algorithm == '2-3 Swap':
        vert_shift = '-400%'
    elif algorithm == '234 Composite':
        vert_shift = '-300%'
    elif algorithm == 'Remainder':
        vert_shift = '-250%'
    elif algorithm == 'Naive':
        vert_shift = '-160%'
    elif algorithm == 'Telescoping':
        vert_shift = '-70%'
    else:
        vert_shift = '0'
    
    # Put label at end of series
    axes.text(
        x[-1],
        y[-1],
        algorithm + '  ',
        style={
            'text-anchor':'start',
            '-toyplot-anchor-shift':'5px',
            'baseline-shift': vert_shift,
        },
    )
    
    # Put a dot at every recorded sample.
    scatter_data = data.loc[grouped_data.groups[(image_size, algorithm)]]
    x = scatter_data['num-processes']
    y = scatter_data['gather-seconds']
    axes.scatterplot(x, y, opacity=1)

<path d="M 45.0 228.646711 L 60.98922755997802 46.61259149999999 L 67.8186256971795 71.47895912500002 L 74.05337771578121 83.94435249999998 L 85.09895928767578 105.40703210000001 L 94.6670772570267 192.6660930625 L 99.01110095052636 200.87110209999997 L 110.65630481700472 201.07099929999998 L 117.48570295420619 201.1783821625 L 126.6455323769828 201.4148123375 L 134.76603654470247 201.3729608125 L 144.3341545140534 201.41330430000002 L 150.7552641046805 201.39022658750002 L 160.32338207403143 209.93055793750003 L 168.76306024856711 210.390910775 L 176.3126096340095 210.229570275 L 185.70136719417962 210.12580001249998 L 194.0012317710801 209.8726113875 L 201.43873352453633 209.9426501125 L 209.99045933105813 209.4506229125 L 218.43013750559385 217.1304418625 L 226.69267233637552 216.544205525 L 235.36844445120636 216.060485075 L 243.6683090281068 214.4788297 L 251.60865106306315 213.89018775 L 260.10398317907953 212.24416342499998 L 268.49419331847537 207.966421325 L 276.71359942881764 203.0161140125 L 285.03552170823303 196.95126942500002 L 293.33538628513344 200.16820610000002 L 301.52583135255367 189.25752133750004 L 309.77106043610627 172.75884125 L 318.16127057550204 147.4275465 L 326.38067668584426 125.71018975 L 334.70259896525977 97.31730012500003 L 343.0024635421601 60.96930362500004" style="stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0;stroke-width:2.0"> 2-3 Swap <path d="M 45.0 228.59688165 L 60.98922755997802 228.25607353750001 L 67.8186256971795 227.98777944999998 L 74.05337771578121 227.91488632500003 L 85.09895928767578 227.86012588749998 L 94.6670772570267 192.3165684375 L 99.01110095052636 191.9978568375 L 110.65630481700472 192.5675214875 L 117.48570295420619 192.75288466249998 L 126.6455323769828 192.47955635000002 L 134.76603654470247 192.5414862375 L 144.3341545140534 201.3502426875 L 150.7552641046805 201.5832999875 L 160.32338207403143 201.71648395 L 168.76306024856711 201.85963322499998 L 176.3126096340095 201.89973141250002 L 185.70136719417962 201.75789505 L 194.0012317710801 210.035515675 L 201.43873352453633 210.11083671249997 L 209.99045933105813 210.2067099875 L 218.43013750559385 210.2899001375 L 226.69267233637552 210.50605264375 L 235.36844445120636 210.331157925 L 243.6683090281068 215.72559482500003 L 251.60865106306315 214.9615550125 L 260.10398317907953 215.4412837625 L 268.49419331847537 215.193628325 L 276.71359942881764 215.29981256250002 L 285.03552170823303 215.5487697625 L 293.33538628513344 200.7245883125 L 301.52583135255367 202.7479899625 L 309.77106043610627 204.87041754999998 L 318.16127057550204 201.4789136875 L 326.38067668584426 200.90732845000002 L 334.70259896525977 198.24535793750002 L 343.0024635421601 51.68857325000003" style="stroke:rgb(98.8%,55.3%,38.4%);stroke-opacity:1.0;stroke-width:2.0"> Naive

In [18]:
toyplot.pdf.render(canvas, 'gather-hdtv.pdf')

In [19]:
image_size = '8K UHD'
algorithms = ['2-3 Swap', 'Naive', 'Remainder', 'Telescoping', '234 Composite', 'IceT']

canvas = toyplot.Canvas('4.5in', '3in')

axes = canvas.cartesian(
    xlabel='Number of Processes',
    ylabel='Gather Time (seconds)',
    xscale='log',
    bounds=(45,-15,15,-50),
)

#axes.x.ticks.locator = toyplot.locator.Log(base=2, format='{:.0f}')
axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=[128, 256, 512, 1024, 2048, 4096, 8192],
)
axes.y.domain.min = 0

for algorithm in algorithms:
    # Plot line following average
    data_series = average_gather[image_size, algorithm]
    x = data_series.index
    y = numpy.array(data_series)
    axes.plot(x, y)
    
    # Some adjustments for correct label placement
    if algorithm == '2-3 Swap':
        vert_shift = '-400%'
    elif algorithm == '234 Composite':
        vert_shift = '-310%'
    elif algorithm == 'Remainder':
        vert_shift = '-200%'
    elif algorithm == 'Naive':
        vert_shift = '-120%'
    elif algorithm == 'Telescoping':
        vert_shift = '70%'
    else:
        vert_shift = '0'
    
    # Put label at end of series
    axes.text(
        x[-1],
        y[-1],
        algorithm + '  ',
        style={
            'text-anchor':'start',
            '-toyplot-anchor-shift':'5px',
            'baseline-shift': vert_shift,
        },
    )
    
    # Put a dot at every recorded sample.
    scatter_data = data.loc[grouped_data.groups[(image_size, algorithm)]]
    x = scatter_data['num-processes']
    y = scatter_data['gather-seconds']
    axes.scatterplot(x, y, opacity=1)

<path d="M 45.0 223.8333265398223 L 60.98922755997802 223.7392876360028 L 67.8186256971795 223.65994130290764 L 74.05337771578121 223.65141283814472 L 85.09895928767578 223.53271751047959 L 94.6670772570267 223.28706934009887 L 99.01110095052636 223.25257163562094 L 110.65630481700472 223.1927078770977 L 117.48570295420619 222.91266199558544 L 126.6455323769828 222.91719395208767 L 134.76603654470247 222.47453308473615 L 144.3341545140534 222.1714468008783 L 150.7552641046805 221.9321498207844 L 160.32338207403143 221.73835626444645 L 168.76306024856711 221.61801265936305 L 176.3126096340095 221.52982820469055 L 185.70136719417962 221.09621512238445 L 194.0012317710801 219.37598120188733 L 201.43873352453633 219.02067903770325 L 209.99045933105813 218.50601005863922 L 218.43013750559385 218.1434793431943 L 226.69267233637552 217.6263460119824 L 235.36844445120636 217.11967327503163 L 243.6683090281068 216.3837254717609 L 251.60865106306315 78.32156069464497 L 260.10398317907953 87.50723979020636 L 268.49419331847537 87.37715167224513 L 276.71359942881764 113.57902106904501 L 285.03552170823303 95.29730207450393 L 293.33538628513344 190.62396859170371 L 301.52583135255367 187.43214872147956 L 309.77106043610627 184.8566588076014 L 318.16127057550204 182.65553430554309 L 326.38067668584426 179.60756292796947 L 334.70259896525977 175.96915341956125 L 343.0024635421601 168.23316818206803" style="stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0;stroke-width:2.0"> 2-3 Swap <path d="M 45.0 221.10836915234918 L 60.98922755997802 223.76403760201114 L 67.8186256971795 223.7902358587451 L 74.05337771578121 223.66787948436817 L 85.09895928767578 223.58651393079586 L 94.6670772570267 223.2557198132339 L 99.01110095052636 223.18854686365438 L 110.65630481700472 223.23354709508698 L 117.48570295420619 223.18224083165305 L 126.6455323769828 223.03300237507702 L 134.76603654470247 222.91436188247275 L 144.3341545140534 222.09193918819233 L 150.7552641046805 222.0647377724034 L 160.32338207403143 222.0687568598068 L 168.76306024856711 221.85547750330514 L 176.3126096340095 221.7656415456226 L 185.70136719417962 221.15059860041137 L 194.0012317710801 219.27997791265156 L 201.43873352453633 219.08451027416086 L 209.99045933105813 214.13895226124112 L 218.43013750559385 218.6619254902755 L 226.69267233637552 218.34154358309732 L 235.36844445120636 218.3132519172744 L 243.6683090281068 216.35644986736017 L 251.60865106306315 216.1841129477859 L 260.10398317907953 215.76132817720796 L 268.49419331847537 215.6683924257897 L 276.71359942881764 215.14742709149976 L 285.03552170823303 215.18985330066275 L 293.33538628513344 188.30361331373868 L 301.52583135255367 188.75198025301367 L 309.77106043610627 185.80849547115338 L 318.16127057550204 185.38903951133008 L 326.38067668584426 192.52561302155502 L 334.70259896525977 192.42916782624044 L 343.0024635421601 163.98147367598858" style="stroke:rgb(98.8%,55.3%,38.4%);stroke-opacity:1.0;stroke-width:2.0"> Naive <g class="toyplot-Datum

In [20]:
toyplot.pdf.render(canvas, 'gather-8k.pdf')